In [46]:
%matplotlib inline

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import os
from sklearn import model_selection, preprocessing
import matplotlib.pyplot as plt
import glob
import re
import time
import seaborn as sns
import xgboost as xgb
import csv
import pickle
color = sns.color_palette()

In [47]:
DATA_PATH = '/kaggle/dev/sberbank-russian-housing-market-data/'
TRAIN_DATA = DATA_PATH + 'train.csv'
TEST_DATA = DATA_PATH + 'test.csv'
MACRO_DATA = DATA_PATH + 'macro.csv'
MODELS_PATH = '/kaggle/dev/ashish/sberbank-russian-housing-market/models/'
SUBMISSIONS_PATH = '/kaggle/dev/sberbank-russian-housing-market-data/submissions/'

In [48]:
train_df = pd.read_csv(TRAIN_DATA)
#macro_df = pd.read_csv(MACRO_DATA)
test_df = pd.read_csv(TEST_DATA)

In [32]:
print(train_df.shape)
train_df

(30471, 292)


id   timestamp  full_sq  life_sq  floor  max_floor  material  \
0          1  2011-08-20       43     27.0    4.0        NaN       NaN   
1          2  2011-08-23       34     19.0    3.0        NaN       NaN   
2          3  2011-08-27       43     29.0    2.0        NaN       NaN   
3          4  2011-09-01       89     50.0    9.0        NaN       NaN   
4          5  2011-09-05       77     77.0    4.0        NaN       NaN   
5          6  2011-09-06       67     46.0   14.0        NaN       NaN   
6          7  2011-09-08       25     14.0   10.0        NaN       NaN   
7          8  2011-09-09       44     44.0    5.0        NaN       NaN   
8          9  2011-09-10       42     27.0    5.0        NaN       NaN   
9         10  2011-09-13       36     21.0    9.0        NaN       NaN   
10        11  2011-09-16       36     19.0   12.0        NaN       NaN   
11        12  2011-09-16       38     19.0   11.0        NaN       NaN   
12        13  2011-09-17       43     28.0    4.0        NaN       NaN   
13        14  2011-09-19       31     31.0    4.0        NaN       NaN   
14        15  2011-09-19       31     21.0    3.0        NaN       NaN   
15        16  2011-09-20       51     31.0   15.0        NaN       NaN   
16        17  2011-09-20       47     31.0    4.0        NaN       NaN   
17        18  2011-09-20       42     28.0    2.0        NaN       NaN   
18        19  2011-09-22       59     33.0   10.0        NaN       NaN   
19        20  2011-09-22       44     29.0    4.0        NaN       NaN   
20        21  2011-09-22       74     44.0   10.0        NaN       NaN   
21        22  2011-09-22       39     39.0    7.0        NaN       NaN   
22        23  2011-09-23       48     34.0    6.0        NaN       NaN   
23        24  2011-09-23       32     18.0    3.0        NaN       NaN   
24        25  2011-09-23       34     19.0   11.0        NaN       NaN   
25        26  2011-09-24       45     29.0    9.0        NaN       NaN   
26        27  2011-09-26       35     20.0    4.0        NaN       NaN   
27        28  2011-09-26       38     20.0    6.0        NaN       NaN   
28        29  2011-09-26       73     38.0   15.0        NaN       NaN   
29        30  2011-09-27       42     27.0    3.0        NaN       NaN   
...      ...         ...      ...      ...    ...        ...       ...   
30441  30444  2015-06-27      113      1.0   26.0       26.0       1.0   
30442  30445  2015-06-27       40     40.0    2.0       12.0       4.0   
30443  30446  2015-06-27       79      NaN   17.0       17.0       1.0   
30444  30447  2015-06-27       85      NaN   20.0       25.0       4.0   
30445  30448  2015-06-27       47     47.0   19.0       25.0       1.0   
30446  30449  2015-06-27       82     82.0    8.0        8.0       6.0   
30447  30450  2015-06-27       64      NaN   15.0       17.0       1.0   
30448  30451  2015-06-27       74      NaN    8.0       17.0       1.0   
30449  30452  2015-06-27       47     47.0    7.0       25.0       1.0   
30450  30453  2015-06-29       65      NaN    5.0        0.0       1.0   
30451  30454  2015-06-29       37      NaN    3.0        3.0       1.0   
30452  30455  2015-06-29       38     19.0    7.0       17.0       1.0   
30453  30456  2015-06-29       45      1.0    6.0       15.0       6.0   
30454  30457  2015-06-29       40     26.0    3.0        9.0       2.0   
30455  30458  2015-06-29       79     79.0    3.0        3.0       1.0   
30456  30459  2015-06-29       52     30.0    8.0       14.0       1.0   
30457  30460  2015-06-29       58     43.0    7.0        9.0       1.0   
30458  30461  2015-06-29       50      1.0    7.0        7.0       1.0   
30459  30462  2015-06-29       51      NaN    4.0       17.0       4.0   
30460  30463  2015-06-29       54     32.0    8.0       16.0       1.0   
30461  30464  2015-06-30       36     19.0    5.0       16.0       1.0   
30462  30465  2015-06-30       47     30.0   23.0       25.0       4.0   
30463  30466  

In [14]:
print(macro_df.shape)
macro_df

NameError: name 'macro_df' is not defined

In [ ]:
plt.figure(figsize=(10,10))
plt.scatter(range(train_df.shape[0]), np.sort(train_df.price_doc.values))
plt.xlabel('index', fontsize=12)
plt.ylabel('price', fontsize=12)
plt.show()

In [ ]:
plt.figure(figsize=(10,10))
sns.distplot(train_df.price_doc.values, bins=50, kde=True)
plt.xlabel('price', fontsize=12)
plt.show()

In [ ]:
plt.figure(figsize=(10,10))
sns.distplot(np.log(train_df.price_doc.values), bins=50, kde=True)
plt.xlabel('price', fontsize=12)
plt.show()

In [ ]:
train_df['yearmonth'] = train_df['timestamp'].apply(lambda x: x[:4] + x[5:7])
grouped_df = train_df.groupby('yearmonth')['price_doc'].aggregate(np.median).reset_index()

In [ ]:
plt.figure(figsize=(16,8))
sns.barplot(grouped_df.yearmonth.values, grouped_df.price_doc.values, alpha=0.8, color=color[2])
plt.ylabel('Median Price', fontsize=16)
plt.xlabel('Year Month', fontsize=16)
plt.xticks(rotation='vertical')
plt.show()

In [ ]:
missing_df = train_df.isnull().sum(axis=0).reset_index()
missing_df.columns = ['column_name', 'missing_count']
missing_df = missing_df.ix[missing_df['missing_count']>0]
missing_df = missing_df.sort_values(['column_name'], ascending=[True])
missing_df

In [ ]:
ind = np.arange(missing_df.shape[0])
plt.figure(figsize=(12,18))
fig, ax = plt.subplots(figsize=(12,18))
rects = ax.barh(ind, missing_df.missing_count.values, color='y')
ax.set_yticks(ind)
ax.set_yticklabels(missing_df.column_name.values, rotation='horizontal')
plt.show()

In [49]:
train_columns = set(train_df.columns)
drop_columns = ['id', 'timestamp', 'price_doc']

for col in drop_columns:
    train_columns.remove(col)

for f in train_columns:
    if train_df[f].dtype=='object':
        lbl = preprocessing.LabelEncoder()
        lbl.fit(list(set(train_df[f].values) | set(test_df[f].values)))
        train_df[f] = lbl.transform(list(train_df[f].values))
        test_df[f] = lbl.transform(list(test_df[f].values))
        
train_df.to_csv(DATA_PATH + 'train_preprocessed.csv')
test_df.to_csv(DATA_PATH + 'test_preprocessed.csv')

In [53]:
train_df = pd.read_csv(DATA_PATH + 'train_preprocessed.csv')
test_df = pd.read_csv(DATA_PATH + 'test_preprocessed.csv')
print('train_df.shape', train_df.shape)
print('test_df.shape', test_df.shape)

train_df.shape (30471, 293)
test_df.shape (7662, 292)


In [54]:
def rmsle(y_predicted, y_true):
    y_pred = y_predicted
    y_label = y_true.get_label()
    temp = np.square(np.log(y_pred + 1.0) - np.log(y_label + 1.0))
    error = np.sqrt(np.sum(temp)/y_pred.shape[0])
    return ("", error)

X = train_df.drop(drop_columns, axis=1)
Y = train_df.price_doc.values

cols = X.columns.values
np_X = X.as_matrix(cols)   

train_X, val_X, train_Y, val_Y = model_selection.train_test_split(np_X, Y, train_size=0.8, random_state=42)

print('train_X.shape', train_X.shape)
print('train_Y.shape', train_Y.shape)
print('val_X.shape', val_X.shape)
print('val_Y.shape', val_Y.shape)
print('np_X.shape', np_X.shape)

train_X.shape (24376, 290)
train_Y.shape (24376,)
val_X.shape (6095, 290)
val_Y.shape (6095,)
np_X.shape (30471, 290)


In [55]:
model = xgb.XGBRegressor(max_depth=8,
                        gamma=0.5,
                        objective="reg:linear",
                        n_estimators=120000,
                        min_child_weight=6,
                        learning_rate=1,
                        nthread=12,
                        subsample=0.70,
                        colsample_bytree=0.70,
                        seed=42,
                        max_delta_step=1)#,
                        #reg_alpha=0.1,
                        #reg_lambda=0.5)

model.fit(train_X, train_Y, eval_set=[(val_X, val_Y)], verbose=True, eval_metric=rmsle, early_stopping_rounds=50)

pickle.dump(model, open(MODELS_PATH + "model-" + str(int(time.time())) + ".xgb", "wb"))

[0]	validation_0-:14.6946
Will train until validation_0- hasn't improved in 50 rounds.
[1]	validation_0-:14.3584
[2]	validation_0-:14.1073
[3]	validation_0-:13.9068
[4]	validation_0-:13.7399
[5]	validation_0-:13.5969
[6]	validation_0-:13.4719
[7]	validation_0-:13.3608
[8]	validation_0-:13.2608
[9]	validation_0-:13.1699
[10]	validation_0-:13.0866
[11]	validation_0-:13.0098
[12]	validation_0-:12.9384
[13]	validation_0-:12.8718
[14]	validation_0-:12.8093
[15]	validation_0-:12.7505
[16]	validation_0-:12.695
[17]	validation_0-:12.6424
[18]	validation_0-:12.5925
[19]	validation_0-:12.5449
[20]	validation_0-:12.4995
[21]	validation_0-:12.4561
[22]	validation_0-:12.4144
[23]	validation_0-:12.3745
[24]	validation_0-:12.3361
[25]	validation_0-:12.2991
[26]	validation_0-:12.2634
[27]	validation_0-:12.229
[28]	validation_0-:12.1957
[29]	validation_0-:12.1634
[30]	validation_0-:12.1322
[31]	validation_0-:12.102
[32]	validation_0-:12.0726
[33]	validation_0-:12.044
[34]	validation_0-:12.0163
[35]	val

[296]	validation_0-:9.91804
[297]	validation_0-:9.9147
[298]	validation_0-:9.91137
[299]	validation_0-:9.90806
[300]	validation_0-:9.90475
[301]	validation_0-:9.90146
[302]	validation_0-:9.89818
[303]	validation_0-:9.8949
[304]	validation_0-:9.89164
[305]	validation_0-:9.88839
[306]	validation_0-:9.88515
[307]	validation_0-:9.88192
[308]	validation_0-:9.8787
[309]	validation_0-:9.87549
[310]	validation_0-:9.87229
[311]	validation_0-:9.8691
[312]	validation_0-:9.86592
[313]	validation_0-:9.86275
[314]	validation_0-:9.85959
[315]	validation_0-:9.85645
[316]	validation_0-:9.85331
[317]	validation_0-:9.85018
[318]	validation_0-:9.84706
[319]	validation_0-:9.84395
[320]	validation_0-:9.84085
[321]	validation_0-:9.83776
[322]	validation_0-:9.83468
[323]	validation_0-:9.83161
[324]	validation_0-:9.82855
[325]	validation_0-:9.82549
[326]	validation_0-:9.82245
[327]	validation_0-:9.81942
[328]	validation_0-:9.81639
[329]	validation_0-:9.81338
[330]	validation_0-:9.81037
[331]	validation_0-:9.80

[590]	validation_0-:9.23382
[591]	validation_0-:9.23214
[592]	validation_0-:9.23046
[593]	validation_0-:9.22878
[594]	validation_0-:9.2271
[595]	validation_0-:9.22543
[596]	validation_0-:9.22376
[597]	validation_0-:9.2221
[598]	validation_0-:9.22044
[599]	validation_0-:9.21878
[600]	validation_0-:9.21712
[601]	validation_0-:9.21546
[602]	validation_0-:9.21381
[603]	validation_0-:9.21216
[604]	validation_0-:9.21051
[605]	validation_0-:9.20887
[606]	validation_0-:9.20723
[607]	validation_0-:9.20559
[608]	validation_0-:9.20396
[609]	validation_0-:9.20232
[610]	validation_0-:9.20069
[611]	validation_0-:9.19906
[612]	validation_0-:9.19744
[613]	validation_0-:9.19582
[614]	validation_0-:9.1942
[615]	validation_0-:9.19258
[616]	validation_0-:9.19096
[617]	validation_0-:9.18935
[618]	validation_0-:9.18774
[619]	validation_0-:9.18614
[620]	validation_0-:9.18453
[621]	validation_0-:9.18293
[622]	validation_0-:9.18133
[623]	validation_0-:9.17973
[624]	validation_0-:9.17814
[625]	validation_0-:9.1

[885]	validation_0-:8.83066
[886]	validation_0-:8.82954
[887]	validation_0-:8.82842
[888]	validation_0-:8.82729
[889]	validation_0-:8.82617
[890]	validation_0-:8.82506
[891]	validation_0-:8.82394
[892]	validation_0-:8.82282
[893]	validation_0-:8.82171
[894]	validation_0-:8.8206
[895]	validation_0-:8.81948
[896]	validation_0-:8.81837
[897]	validation_0-:8.81726
[898]	validation_0-:8.81615
[899]	validation_0-:8.81505
[900]	validation_0-:8.81394
[901]	validation_0-:8.81283
[902]	validation_0-:8.81173
[903]	validation_0-:8.81063
[904]	validation_0-:8.80953
[905]	validation_0-:8.80843
[906]	validation_0-:8.80733
[907]	validation_0-:8.80623
[908]	validation_0-:8.80514
[909]	validation_0-:8.80404
[910]	validation_0-:8.80295
[911]	validation_0-:8.80185
[912]	validation_0-:8.80076
[913]	validation_0-:8.79967
[914]	validation_0-:8.79858
[915]	validation_0-:8.7975
[916]	validation_0-:8.79641
[917]	validation_0-:8.79532
[918]	validation_0-:8.79424
[919]	validation_0-:8.79316
[920]	validation_0-:8.

[1173]	validation_0-:8.5503
[1174]	validation_0-:8.54945
[1175]	validation_0-:8.5486
[1176]	validation_0-:8.54776
[1177]	validation_0-:8.54691
[1178]	validation_0-:8.54606
[1179]	validation_0-:8.54522
[1180]	validation_0-:8.54438
[1181]	validation_0-:8.54353
[1182]	validation_0-:8.54269
[1183]	validation_0-:8.54185
[1184]	validation_0-:8.54101
[1185]	validation_0-:8.54017
[1186]	validation_0-:8.53933
[1187]	validation_0-:8.53849
[1188]	validation_0-:8.53765
[1189]	validation_0-:8.53681
[1190]	validation_0-:8.53598
[1191]	validation_0-:8.53514
[1192]	validation_0-:8.5343
[1193]	validation_0-:8.53347
[1194]	validation_0-:8.53264
[1195]	validation_0-:8.5318
[1196]	validation_0-:8.53097
[1197]	validation_0-:8.53014
[1198]	validation_0-:8.52931
[1199]	validation_0-:8.52848
[1200]	validation_0-:8.52765
[1201]	validation_0-:8.52682
[1202]	validation_0-:8.52599
[1203]	validation_0-:8.52516
[1204]	validation_0-:8.52433
[1205]	validation_0-:8.52351
[1206]	validation_0-:8.52268
[1207]	validation_

...

[118755]	validation_0-:3.95977
[118756]	validation_0-:3.95976
[118757]	validation_0-:3.95975
[118758]	validation_0-:3.95974
[118759]	validation_0-:3.95974
[118760]	validation_0-:3.95973
[118761]	validation_0-:3.95972
[118762]	validation_0-:3.95971
[118763]	validation_0-:3.9597
[118764]	validation_0-:3.95969
[118765]	validation_0-:3.95969
[118766]	validation_0-:3.95968
[118767]	validation_0-:3.95967
[118768]	validation_0-:3.95966
[118769]	validation_0-:3.95965
[118770]	validation_0-:3.95965
[118771]	validation_0-:3.95964
[118772]	validation_0-:3.95963
[118773]	validation_0-:3.95962
[118774]	validation_0-:3.95961
[118775]	validation_0-:3.9596
[118776]	validation_0-:3.9596
[118777]	validation_0-:3.95959
[118778]	validation_0-:3.95958
[118779]	validation_0-:3.95957
[118780]	validation_0-:3.95956
[118781]	validation_0-:3.95955
[118782]	validation_0-:3.95954
[118783]	validation_0-:3.95954
[118784]	validation_0-:3.95953
[118785]	validation_0-:3.95952
[118786]	validation_0-:3.95951
[118787]	va

[119021]	validation_0-:3.95756
[119022]	validation_0-:3.95755
[119023]	validation_0-:3.95754
[119024]	validation_0-:3.95753
[119025]	validation_0-:3.95752
[119026]	validation_0-:3.95752
[119027]	validation_0-:3.95751
[119028]	validation_0-:3.9575
[119029]	validation_0-:3.95749
[119030]	validation_0-:3.95748
[119031]	validation_0-:3.95748
[119032]	validation_0-:3.95747
[119033]	validation_0-:3.95746
[119034]	validation_0-:3.95745
[119035]	validation_0-:3.95744
[119036]	validation_0-:3.95743
[119037]	validation_0-:3.95743
[119038]	validation_0-:3.95742
[119039]	validation_0-:3.95741
[119040]	validation_0-:3.9574
[119041]	validation_0-:3.95739
[119042]	validation_0-:3.95738
[119043]	validation_0-:3.95738
[119044]	validation_0-:3.95737
[119045]	validation_0-:3.95736
[119046]	validation_0-:3.95735
[119047]	validation_0-:3.95734
[119048]	validation_0-:3.95734
[119049]	validation_0-:3.95733
[119050]	validation_0-:3.95732
[119051]	validation_0-:3.95731
[119052]	validation_0-:3.9573
[119053]	va

[119287]	validation_0-:3.95535
[119288]	validation_0-:3.95534
[119289]	validation_0-:3.95534
[119290]	validation_0-:3.95533
[119291]	validation_0-:3.95532
[119292]	validation_0-:3.95531
[119293]	validation_0-:3.9553
[119294]	validation_0-:3.9553
[119295]	validation_0-:3.95529
[119296]	validation_0-:3.95528
[119297]	validation_0-:3.95527
[119298]	validation_0-:3.95526
[119299]	validation_0-:3.95525
[119300]	validation_0-:3.95525
[119301]	validation_0-:3.95524
[119302]	validation_0-:3.95523
[119303]	validation_0-:3.95522
[119304]	validation_0-:3.95521
[119305]	validation_0-:3.9552
[119306]	validation_0-:3.9552
[119307]	validation_0-:3.95519
[119308]	validation_0-:3.95518
[119309]	validation_0-:3.95517
[119310]	validation_0-:3.95516
[119311]	validation_0-:3.95515
[119312]	validation_0-:3.95515
[119313]	validation_0-:3.95514
[119314]	validation_0-:3.95513
[119315]	validation_0-:3.95512
[119316]	validation_0-:3.95511
[119317]	validation_0-:3.9551
[119318]	validation_0-:3.9551
[119319]	valid

[119553]	validation_0-:3.95315
[119554]	validation_0-:3.95314
[119555]	validation_0-:3.95313
[119556]	validation_0-:3.95313
[119557]	validation_0-:3.95312
[119558]	validation_0-:3.95311
[119559]	validation_0-:3.9531
[119560]	validation_0-:3.95309
[119561]	validation_0-:3.95309
[119562]	validation_0-:3.95308
[119563]	validation_0-:3.95307
[119564]	validation_0-:3.95306
[119565]	validation_0-:3.95305
[119566]	validation_0-:3.95304
[119567]	validation_0-:3.95303
[119568]	validation_0-:3.95303
[119569]	validation_0-:3.95302
[119570]	validation_0-:3.95301
[119571]	validation_0-:3.953
[119572]	validation_0-:3.95299
[119573]	validation_0-:3.95299
[119574]	validation_0-:3.95298
[119575]	validation_0-:3.95297
[119576]	validation_0-:3.95296
[119577]	validation_0-:3.95295
[119578]	validation_0-:3.95295
[119579]	validation_0-:3.95294
[119580]	validation_0-:3.95293
[119581]	validation_0-:3.95292
[119582]	validation_0-:3.95291
[119583]	validation_0-:3.9529
[119584]	validation_0-:3.95289
[119585]	val

[119819]	validation_0-:3.95095
[119820]	validation_0-:3.95095
[119821]	validation_0-:3.95094
[119822]	validation_0-:3.95093
[119823]	validation_0-:3.95092
[119824]	validation_0-:3.95091
[119825]	validation_0-:3.95091
[119826]	validation_0-:3.9509
[119827]	validation_0-:3.95089
[119828]	validation_0-:3.95088
[119829]	validation_0-:3.95087
[119830]	validation_0-:3.95086
[119831]	validation_0-:3.95086
[119832]	validation_0-:3.95085
[119833]	validation_0-:3.95084
[119834]	validation_0-:3.95083
[119835]	validation_0-:3.95082
[119836]	validation_0-:3.95081
[119837]	validation_0-:3.95081
[119838]	validation_0-:3.9508
[119839]	validation_0-:3.95079
[119840]	validation_0-:3.95078
[119841]	validation_0-:3.95077
[119842]	validation_0-:3.95077
[119843]	validation_0-:3.95076
[119844]	validation_0-:3.95075
[119845]	validation_0-:3.95074
[119846]	validation_0-:3.95073
[119847]	validation_0-:3.95072
[119848]	validation_0-:3.95072
[119849]	validation_0-:3.95071
[119850]	validation_0-:3.9507
[119851]	va

In [16]:
train_X

array([[46, nan, 4.0, ..., 0, 6, 1],
       [134, nan, 2.0, ..., 0, 0, 0],
       [44, 28.0, 6.0, ..., 8, 82, 12],
       ..., 
       [59, 41.0, 4.0, ..., 7, 44, 7],
       [64, 33.0, 2.0, ..., 0, 6, 1],
       [33, 13.0, 15.0, ..., 0, 13, 1]], dtype=object)

In [17]:
test_X = test_df.drop(['timestamp'], axis=1)
test_columns_set = set(test_X.columns.values)
test_X

id  full_sq  life_sq  floor  max_floor  material  build_year  \
0     30474    39.00    20.70      2          9         1      1998.0   
1     30475    79.20      NaN      8         17         1         0.0   
2     30476    40.50    25.10      3          5         2      1960.0   
3     30477    62.80    36.00     17         17         1      2016.0   
4     30478    40.00    40.00     17         17         1         0.0   
5     30479    48.43      NaN     21          1         1      2015.0   
6     30480    38.80      NaN     15         17         1         NaN   
7     30481    43.10      NaN      5          0         1         NaN   
8     30482    45.40    28.50      9         12         5      1972.0   
9     30483    43.30    43.30      7         22         1         0.0   
10    30484    37.26      NaN      4         15         4      2017.0   
11    30485    39.20    10.00     11         17         4         0.0   
12    30486    37.04    37.04     14         15         6      2015.0   
13    30487    39.80    18.90      4         17         1      2013.0   
14    30488    69.30      NaN      7          1         1         NaN   
15    30489    69.30      NaN     10          0         1         NaN   
16    30490   117.40      NaN     10          0         1         NaN   
17    30491    94.50    61.90      2         12         1      2000.0   
18    30492    62.50    32.60      7         17         1      2013.0   
19    30493    77.70    52.60      2          5         5      1958.0   
20    30494    64.00    64.00      4         17         1         0.0   
21    30495    67.20    45.10     14         16         5      1978.0   
22    30496    99.88      NaN      4          9         1         NaN   
23    30497    79.20      NaN      6         17         1         NaN   
24    30498    32.50    18.70      4          9         1      1971.0   
25    30499    65.10    46.00     11         12         1      1978.0   
26    30500    74.00    41.70     17         17         1      2016.0   
27    30501    45.80    29.60      6          9         1      1969.0   
28    30502    32.00    32.00     15         17         1      2017.0   
29    30503    37.80    19.10     13         16         1      1982.0   
...     ...      ...      ...    ...        ...       ...         ...   
7632  38106    44.40    27.90      6          9         1      1967.0   
7633  38107    37.93    37.93      3         13         1         0.0   
7634  38108    64.60    46.20      6         16         5      1984.0   
7635  38109    42.23     1.00     11         17         1         NaN   
7636  38110    57.90    36.90      2          3         1      1953.0   
7637  38111    54.09    54.09     12         17         4      2017.0   
7638  38112    36.50      NaN     13         17         1         NaN   
7639  38113    51.30    30.60      5         17         1      1996.0   
7640  38114    77.51     1.00      4          1         1         1.0   
7641  38115    36.00    36.00     10         17         1      2015.0   
7642  38116    43.71    43.71      6         20         1         NaN   
7643  38117    64.30    33.90     15         17         1      2013.0   
7644  38118    48.40    30.20      4         30         6      2012.0   
7645  38119    39.90      NaN     11         16         1      2016.0   
7646  38120    69.70     1.00      8          1         4      2016.0   
7647  38121    39.60    18.90     22         25         1      2014.0   
7648  38122    33.89     1.00      3          1         1         1.0   
7649  38123    27.27      NaN     14          1         1         NaN   
7650  38124    64.00     1.00     12         17         1      2017.0   
7651  38125    54.60    32.20     16         16         1      2000.0   
7652  38126    62.39    40.00      4         16         1      2016.0   
7653  38127    19.91     1.00      8          1         1         1.0   
7654  38128    23.56     1.00      1          1         1         1

In [24]:
model = pickle.load(open(MODELS_PATH + 'model-1494567164.xgb', 'rb'))
filename = SUBMISSIONS_PATH + 'submission-' + str(int(time.time())) + ".csv"

with open(filename, 'w') as csvfile:
    submission_writer = csv.writer(csvfile, delimiter=',')
    submission_writer.writerow(['id', 'price_doc'])

    t_cols = ['id'] + list(cols)
    np_test_X = test_X.as_matrix(t_cols)
    
    print('\nPredicting on test set ', np_test_X.shape)
    for idx in range(np_test_X.shape[0]):        
        r_id = np_test_X[idx, 0]
        x = np_test_X[idx, 1:].reshape((-1, 1))
        print(x.shape)
        try:
            y = model.predict(x)
        except ValueError as error:
            for idx in range(len(t_cols[1:])):
                print(t_cols[1+idx], x[idx])
            print(error)
        #print(y)
        break
        submission_writer.writerow([r_id, y[0]])

print('Generated submission file: {}'.format(filename))


Predicting on test set  (7662, 290)
(289, 1)
full_sq [39.0]
life_sq [20.7]
floor [2]
max_floor [9]
material [1]
build_year [1998.0]
num_room [1]
kitch_sq [8.9]
state [3.0]
product_type ['Investment']
sub_area ['Juzhnoe Butovo']
area_m [26155137.04]
raion_popul [178264]
green_zone_part [0.137846204]
indust_part [0.041116354]
children_preschool [14080]
preschool_quota [11926.0]
preschool_education_centers_raion [11]
children_school [14892]
school_quota [24750.0]
school_education_centers_raion [13]
school_education_centers_top_20_raion [1]
hospital_beds_raion [nan]
healthcare_centers_raion [1]
university_top_20_raion [0]
sport_objects_raion [13]
additional_education_raion [4]
culture_objects_top_25 ['no']
culture_objects_top_25_raion [0]
shopping_centers_raion [4]
office_raion [4]
thermal_power_plant_raion ['no']
incineration_raion ['no']
oil_chemistry_raion ['no']
radiation_raion ['no']
railroad_terminal_raion ['no']
big_market_raion ['no']
nuclear_reactor_raion ['no']
detention_facilit

Exception ignored in: <bound method DMatrix.__del__ of <xgboost.core.DMatrix object at 0x7fa43e52fe48>>
Traceback (most recent call last):
  File "/kaggle/dev/ashish/sberbank-russian-housing-market/sber/lib/python3.5/site-packages/xgboost/core.py", line 324, in __del__
    _check_call(_LIB.XGDMatrixFree(self.handle))
AttributeError: 'DMatrix' object has no attribute 'handle'
